# Running ALF

In [ ]:
from pprint import pprint  # Pretty print
from py_alf import ALF_source, Simulation  # Interface with ALF

## ALF_source
Create instance of `ALF_source`, choosing to checkout the git branch `'211-add-nematic-dirac-hamiltonian'`, since the Nematic Dirac Hamiltonian is not on master.

Reminder: Directory containing the ALF code is taken from environment variable `$ALF_DIR`, if present.

In [ ]:
alf_src = ALF_source(
    branch='211-add-nematic-dirac-hamiltonian',
)

Checking out branch 211-add-nematic-dirac-hamiltonian
Your branch is up to date with 'origin/211-add-nematic-dirac-hamiltonian'.


Switched to branch '211-add-nematic-dirac-hamiltonian'


Check available Hamiltonians:

In [ ]:
alf_src.get_ham_names()

['Kondo',
 'Hubbard',
 'Hubbard_Plain_Vanilla',
 'tV',
 'LRC',
 'Z2_Matter',
 'Nematic_Dirac']

Print valid parameters and their defaults for Nematic Dirac Hamiltonian:

In [ ]:
pprint(alf_src.get_default_params('Nematic_Dirac', include_generic=False))

OrderedDict([('VAR_Nematic_Dirac',
              {'Global_J': {'comment': 'J for proposing global updates',
                            'defined_in_base': False,
                            'value': 1.0},
               'Global_h': {'comment': 'h for proposing global updates',
                            'defined_in_base': False,
                            'value': 3.0},
               'Global_type': {'comment': 'Type of global update. Possible '
                                          "values: 'Wolff', 'Geo', 'switch', "
                                          "'flip'",
                               'defined_in_base': False,
                               'value': ''},
               'Ham_J': {'comment': 'Ferromagnetic Ising interaction',
                         'defined_in_base': False,
                         'value': 1.0},
               'Ham_chem': {'comment': 'Chemical potential',
                            'defined_in_base': False,
                            'value': 0

## Perform simulations

The loop shown below performs a parameter sweep over transverse field strength $h \in \{2.5, 3.0, 3.5, 4.0\}$ for system sizes $L \in \{4, 6, 8, 10\}$.
Parallel Tempering is used to run simulations with different $h$ in parallel. This method is actually intended for addressing ergodicity issues, but in this case it is only used to more conveniently perform a parameter sweep in parallel.

The simulations are set to take $0.2$, $1$, $7$ and $18$ hours.

In [5]:
for L, time in zip([4, 6, 8, 10], [.2, 1., 7., 18.]):
    print(f'====== L={L} ======')
    sim = Simulation(
        alf_src,
        'Nematic_Dirac',
        [{
            # Model specific parameters
            'Model_vers': 1,  # C_2v model
            'L1': L,
            'L2': L,
            'beta': L*4.,
            'Ham_xi': 0.25,
            'Ham_h': h,
            # QMC parameters
            'Ltau': 1,
            'CPU_MAX': time,
            'NSweep': 20,
            'mpi_per_parameter_set': 1,
            # Only put Tempering_calc_det=False if you know what you're doing.
            'Tempering_calc_det': False,  
        } for h in [2.5, 3.0, 3.5, 4.0]],
        machine='intel',
        mpi=True,
        n_mpi=4,
    )
    if L == 4:
        # We only need to compile once
        sim.compile()
    sim.run()
    sim.print_info_file()

====== L=4 ======
Compiling ALF... 
Cleaning up Prog/
Cleaning up Libraries/
Cleaning up Analysis/
Compiling Libraries


ar: creating modules_90.a
ar: creating libqrref.a


Compiling Analysis
Compiling Program
Parsing Hamiltonian parameters
filename: Hamiltonians/Hamiltonian_Kondo_smod.F90
filename: Hamiltonians/Hamiltonian_Hubbard_smod.F90
filename: Hamiltonians/Hamiltonian_Hubbard_Plain_Vanilla_smod.F90
filename: Hamiltonians/Hamiltonian_tV_smod.F90
filename: Hamiltonians/Hamiltonian_LRC_smod.F90
filename: Hamiltonians/Hamiltonian_Z2_Matter_smod.F90
filename: Hamiltonians/Hamiltonian_Nematic_Dirac_smod.F90
Compiling program modules
Link program
Done.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/ALF_data/temper_Nematic_Dirac_Model_vers=1_L1=4_L2=4_beta=16.0_xi=0.25_h=2.5" for Monte Carlo run.
Create new directory.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/ALF_data/temper_Nematic_Dirac_Model_vers=1_L1=4_L2=4_beta=16.0_xi=0.25_h=2.5/Temp_0" for Monte Carlo run.
Create new directory.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/ALF_data/temper_Nematic_Dirac_Model_vers=1_L1=4_L2=4_

The text printed through these simulations is very long and has therefore been hidden, but it can be viewed in the [website version](https://purl.org/diss-jschwab) of this document.

The info files produced by ALF show a "Precision Green" and "Precision Phase" of order $10^{-14}$ which is very good and much smaller than $10^{-8}$. In fact one might consider increasing the stabilization interval `Nwrap` to speed up the simulation.

The produced QMC data will be postprocessed in the next section.

## Prepare directories for simulation

pyALF can also be use to prepare simulation directories without executing ALF, for example to copy the prepared directories to another machine or execute ALF in another way like a scheduler.

The following example prepares the directory `for_hpc` with subdirectories `L{L}/h{h}`.

In [6]:
for L in [4, 6, 8, 10]:
    for h in [2.5, 3.0, 3.5, 4.0]:
        sim = Simulation(
            alf_src,
            'Nematic_Dirac',
            {
                # Model specific parameters
                'Model_vers': 1,  # C_2v model
                'L1': L,
                'L2': L,
                'beta': L*4.,
                'Ham_xi': 0.25,
                'Ham_h': h,
                # QMC parameters
                'Ltau': 1,
                'CPU_MAX': 24,
                'NSweep': 20,
                'mpi_per_parameter_set': 1,
                # Only put Tempering_calc_det=False if you know what you're doing.
                'Tempering_calc_det': False,  
            },
            machine='intel',
            mpi=True,
            n_mpi=4,
            sim_root='for_hpc',
            sim_dir=f'L{L}/h{h}'
        )
        sim.run(only_prep=True)

Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/for_hpc/L4/h2.5" for Monte Carlo run.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/for_hpc/L4/h3.0" for Monte Carlo run.
Create new directory.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/for_hpc/L4/h3.5" for Monte Carlo run.
Create new directory.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/for_hpc/L4/h4.0" for Monte Carlo run.
Create new directory.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/for_hpc/L6/h2.5" for Monte Carlo run.
Create new directory.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/for_hpc/L6/h3.0" for Monte Carlo run.
Create new directory.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/for_hpc/L6/h3.5" for Monte Carlo run.
Create new directory.
Prepare directory "/home/jonas/dissertation/jb/appendix_nematic_pyalf/for_hpc/L6/h4.0" for Monte Carlo run.
Crea

In [10]:
!tree for_hpc

for_hpc
├── L10
│   ├── h2.5
│   │   ├── parameters
│   │   └── seeds
│   ├── h3.0
│   │   ├── parameters
│   │   └── seeds
│   ├── h3.5
│   │   ├── parameters
│   │   └── seeds
│   └── h4.0
│       ├── parameters
│       └── seeds
├── L4
│   ├── h2.5
│   │   ├── parameters
│   │   └── seeds
│   ├── h3.0
│   │   ├── parameters
│   │   └── seeds
│   ├── h3.5
│   │   ├── parameters
│   │   └── seeds
│   └── h4.0
│       ├── parameters
│       └── seeds
├── L6
│   ├── h2.5
│   │   ├── parameters
│   │   └── seeds
│   ├── h3.0
│   │   ├── parameters
│   │   └── seeds
│   ├── h3.5
│   │   ├── parameters
│   │   └── seeds
│   └── h4.0
│       ├── parameters
│       └── seeds
└── L8
    ├── h2.5
    │   ├── parameters
    │   └── seeds
    ├── h3.0
    │   ├── parameters
    │   └── seeds
    ├── h3.5
    │   ├── parameters
    │   └── seeds
    └── h4.0
        ├── parameters
        └── seeds

20 directories, 32 files
